In [1]:
import pandas as pd
%matplotlib inline

In [2]:
#read data from csv files
how_much = pd.read_csv('items_number.csv', sep = ';')
items = pd.read_csv('items.csv', sep = ';')
paths = pd.read_csv('paths.csv', sep = ';')
machines = pd.read_csv('machines.csv', sep = ',')
norm_times = pd.read_csv('norm_time.csv', sep = ';')
setup_times = pd.read_csv('setup_time.csv', sep = ';')

In [3]:
#some setups to correct data
setup_times.fillna(value = 10, inplace = True) #fill blank fields
norm_times.fillna(value = '-', inplace = True)
paths.fillna(value = -1, inplace = True)
how_much = how_much[0:72] #cut useless definitions

pd.options.display.max_rows = 100
N_DETAILS = 72
N_MACHINES = 10

In [4]:
machines.head(15)
unique_machines = {'Пила' : 0, 'Плазменная' : 1, 'Токарный' : 2, 'Фрезерный' : 3, 
                   'Сверление' : 4, 'Сварка' : 5, 'Окраска' : 6}
paths.replace(unique_machines, inplace = True)
paths.head(N_DETAILS)

№           Номенклатура Тип оборудования  Unnamed: 3  Unnamed: 4  \
0   -1.0                     -1       операция 1  операция 2  операция 3   
1    1.0           Переходник 1                5           6          -1   
2    1.1               Муфта А1                0           2           3   
3    1.2               Муфта А2                0           2           3   
4    2.0           Переходник 2                5           6          -1   
5    2.1               Муфта Б1                0           2           3   
6    2.2               Муфта Б2                0           2           3   
7    3.0                Ролик 1                5           6          -1   
8    3.1              Корпус 1В                3           2           4   
9    3.2  Ось эксцентриковая 2В                0           2          -1   
10   3.3    Фланец-заготовка 3В                0           2           4   
11   3.4       Ось-заготовка 4В                0           2          -1   
12   3.5              Колесо 5В                0           2           3   
13   3.6             Бобышка 6В                0           2           3   
14   4.0                Ролик 2                5           6          -1   
15   4.1              Корпус 1С                3           2           4   
16   4.2  Ось эксцентриковая 2С                0           2          -1   
17   4.3    Фланец-заготовка 3С                0           2           4   
18   4.4       Ось-заготовка 4С                0           2          -1   
19   4.5              Колесо 5С                0           2           3   
20   4.6             Бобышка 6С                0           2           3   
21   5.0        Ролик каретки 3                5           6          -1   
22   5.1               Шайба 1Д                0           2          -1   
23   5.2               Шайба 2Д                0           2          -1   
24   5.3               Ролик 3Д                0           2           3   
25   5.4              Крышка 4Д                1           2           4   
26   5.5              Втулка 5Д                0           2           3   
27   5.6             Вставка 6Д                1           2           3   
28   6.0             Изделие №6                1           2           3   
29   7.0             Изделие №7                1           3           4   
30   8.0             Изделие №8                1           2          -1   
31   9.0             Изделие №9                1           3           2   
32  10.0            Изделие №10                1           2          -1   
33  11.0            Изделие №11                1           3           4   
34  12.0            Изделие №12                1           2          -1   
35  13.0            Изделие №13                1           3           2   
36  14.0            Изделие №14                1           2          -1   
37  15.0            Изделие №15                1           3           4   
38  16.0            Изделие №16                0           2          -1   
39  17.0            Изделие №17                0           3           4   
40  18.0            Изделие №18                1           2          -1   
41  19.0            Изделие №19                1           3           2   
42  20.0            Изделие №20                0           2           3   
43  21.0            Изделие №21                0           3           2   
44  22.0            Изделие №22                1           2          -1   
45  23.0            Изделие №23                1           3           2   
46  24.0            Изделие №24                0           2           3   
47  25.0            Изделие №25                0           3           4   
48  26.0            Изделие №26                1           2          -1   
49  27.0            Изделие №27                1           3          -1   
50  28.0            Изделие №28                0           2           3   
51  29.0            Изделие №29                0       

In [5]:
class step:
    def __init__(self, machine, time, setup):
        self.machine_ = machine
        self.time_ = time
        self.setup_ = setup

In [6]:
class detail_type:
    def __init__(self, n, path, n_steps): #path - is an array of class step
        self.number_ = n
        self.n_steps_ = n_steps
        self.path_ = path

In [7]:
class dtype_state:
    def __init__(self, detail_type, n_to_do):
        self.detail_type_ = detail_type
        self.n_to_do_ = n_to_do
        self.done_ = 0
        self.cur_step_ = 0
        self.is_being_processed_ = 0
        self.details_progress_ = [detail(detail_type.n_steps_) for i in range(n_to_do)] #array of details
        self.needed_details_ = [] #-1 if simple detail; array of 'sub'-details if complex
        self.remaining_time_ = 0

In [8]:
class detail:
    def __init__(self, n_steps):
        self.progress_ = [0 for i in range(n_steps)]

In [9]:
State = [] #array of dtype_states

for i in range(N_DETAILS):        # in this cycle we initialize State
    #make path for the type
    j = 2
    path = []
    machine_type = paths.iloc[i + 1, j]
    while machine_type != -1:
        one_step = step(machine_type, 
                    norm_times.iloc[i, machine_type + 2],
                   setup_times.iloc[i, machine_type + 2])
        path.append(one_step)
        j += 1
        if j > 6:
            break
        machine_type = paths.iloc[i + 1, j]
        
    this_type = detail_type(i, path, j - 2)
    
    n_to_do = how_much['Кол-во'][i]
    state_elem = dtype_state(this_type, int(n_to_do))
    State.append(state_elem)
    
for i in range(N_DETAILS):
    rest = int ((how_much.iloc[i, 0] * 10) % 10)
    if rest != 0:
        State[i - rest].needed_details_.append(i)

for i in range(N_DETAILS):
    time_per_detail = 0
    for j in range(State[i].detail_type_.n_steps_):
        time_per_detail += State[i].detail_type_.path_[j].time_
    State[i].remaining_time = time_per_detail * State[i].n_to_do_
    
# for i in range(N_DETAILS):
#     print (len (State[i].needed_details_))
    
# for i in range(N_DETAILS):
#     print ("------", i)
#     for j in range (len (State[i].detail_type_.path_)):
#         print (int (State[i].detail_type_.path_[j].machine_))


In [10]:
class machine:
    def __init__(self, mtype):
        self.machine_type_ = mtype
        self.processing_detail_ = [-1, -1] #[0] - type of the detail and [1] - number in details_progress array
        self.busy = 0
        
    # machine does not start before previous work haven't finished
    def what_available(self):
        available_details = []
        for i in range(len(State)):
            if (State[i].is_being_processed_ == 0) and (State[i].done_ == 0):
                ready = 1  
                for j in range(len(State[i].needed_details_)):
                    if (State[State[i].needed_details_[j]].done_ == 0):
                        ready = 0
                        break
#                 if (State[i].cur_step_ > 0):
#                     print ("i = ", i, "cur_step = ", State[i].cur_step_, "len = ", len(State[i].detail_type_.path_))
                if (State[i].detail_type_.path_[State[i].cur_step_].machine_ == self.machine_type_) and (ready == 1):
                    available_details.append(i)

        
        return available_details
    
    def long_job_first(self):
        available = self.what_available()
        if (len(available) == 0): #there is nothing to do
            return -1
        
        best = 0
        for i in range(len(available)):
            if (State[available[i]].remaining_time > State[best].remaining_time):
                best = i
        
        return best
    
    def processing (self):
        if (self.busy == 0):
            self.processing_detail_[0] = self.long_job_first()
            self.processing_detail_[1] = 0
            if (self.processing_detail_[0] != -1):
            
                self.busy = 1
                State[self.processing_detail_[0]].is_being_processed_ = 1
                
        if (self.busy == 1):
            i = self.processing_detail_[0]
            
            State[i].details_progress_[self.processing_detail_[1]].progress_[State[i].cur_step_] += 1
            State[i].remaining_time_ -= 1
            
            if (State[i].detail_type_.path_[State[i].cur_step_].time_ == 
                State[i].details_progress_[self.processing_detail_[1]].progress_[State[i].cur_step_]):
            # если процедура над деталью завершилась
                
                if (self.processing_detail_[1] != State[i].n_to_do_ - 1):
                # если это НЕ последняя деталь в партии
                    self.processing_detail_[1] += 1
                
                else:
                # если это последняя деталь в партии
                    self.busy = 0
                    State[self.processing_detail_[0]].is_being_processed_ = 0
                    if (State[i].cur_step_ == State[i].detail_type_.n_steps_ - 1):
                    # если это последний этап последней детали
                        State[i].done_ = 1
                        State.pop(i)
                    else:
                    # если не последний этап последней детали
                        State[i].cur_step_ += 1
                
                
#                 if (State[i].cur_step_ == State[i].detail_type_.n_steps_):
#                 # если это последний этап данной детали
#                     if (self.processing_detail_[1] == State[i].n_to_do - 1):
#                     # если это последний этап последней детали
#                         State[i].done_ = 1
#                         State[i].cur_step_ += 1
#                         self.busy = 0
                
                
        

In [11]:
machineA = machine (3)
print (machineA.what_available())

[7, 14, 61, 63, 66, 68, 70]


In [12]:
Factory = []

for i in range (N_MACHINES):
    mtype = unique_machines[machines.iloc[i, 2]]
    Factory.append(machine(mtype))

In [13]:
t = 0
while (len(State) > 0):
    print ("len(State) = ", len(State))
    for k in range (len (Factory)):
        Factory[k].processing()
    t += 1
        
print ("T = ", t)
        

len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  72
len(State) =  

len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  

len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  

len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  

len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  

...

len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  

len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  

len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  

len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  62
len(State) =  

KeyboardInterrupt: 